In [2]:
from qiskit import QuantumCircuit
from qiskit_aer import AerSimulator
from qiskit.transpiler.preset_passmanagers import generate_preset_pass_manager
from qiskit_ibm_runtime import SamplerV2 as Sampler

# 创建一个4比特的量子电路和1比特的经典寄存器，用于记录辅助比特的测量结果
qc = QuantumCircuit(4, 4)

# 假设比特1,2,3已经被你制备成需要的叠加态
# 例如，你可以在此处添加状态制备代码
# qc.ry(..., 1)
# qc.ry(..., 2)
# qc.ry(..., 3)

# 1. 对辅助比特（0号）施加 Hadamard 门
qc.h(0)

qc.x(0)
qc.h(1)
# 2. 以辅助比特为控制位，对每个测试比特施加 CZ 门
for target in [1, 2, 3]:
    qc.cz(0, target)

# 3. 再对辅助比特施加 Hadamard 门
qc.h(0)

# 4. 测量辅助比特到经典寄存器（仅测量辅助比特）
qc.measure(range(4), range(4))

# 打印电路
print(qc.draw())

sampler = Sampler(mode=AerSimulator())
job = sampler.run([qc], shots=1024)

# 获取结果
result = job.result()
pub_result = result[0]

# 提取每次测量的结果
counts = pub_result.data.c.get_counts()
print("Measurement counts:", counts)

     ┌───┐┌───┐            ┌───┐   ┌─┐
q_0: ┤ H ├┤ X ├─■──■─────■─┤ H ├───┤M├
     ├───┤└───┘ │  │ ┌─┐ │ └───┘   └╥┘
q_1: ┤ H ├──────■──┼─┤M├─┼──────────╫─
     └───┘         │ └╥┘ │  ┌─┐     ║ 
q_2: ──────────────■──╫──┼──┤M├─────╫─
                      ║  │  └╥┘ ┌─┐ ║ 
q_3: ─────────────────╫──■───╫──┤M├─╫─
                      ║      ║  └╥┘ ║ 
c: 4/═════════════════╩══════╩═══╩══╩═
                      1      2   3  0 
Measurement counts: {'0011': 525, '0000': 499}


In [1]:
import numpy as np

A = np.array([[1, 2, -3], [1, 0, 1]])  # 系统矩阵
b = np.array([0, 2])           # 常数向量

# 使用最小二乘法求解 Ax = b
x, residuals, rank, s = np.linalg.lstsq(A, b, rcond=None)
print("特解为：", x)


特解为： [1.33333333 0.33333333 0.66666667]


In [ ]:
from qiskit import QuantumCircuit
from qiskit_aer import AerSimulator
from qiskit.transpiler.preset_passmanagers import generate_preset_pass_manager
from qiskit_ibm_runtime import SamplerV2 as Sampler

# 创建量子电路
qc = QuantumCircuit(5, 5)
for i in range(1000):
    qc.h(0)
    qc.measure(range(1), range(1))
    qc.h(0) 
    qc.measure(range(1), range(1))
    qc.h(1)
    qc.h(1) 
    qc.h(2)
    qc.h(2) 

# 打印电路
print(qc.draw())

# 初始化模拟器
aer = AerSimulator()
CORE_BASIS_GATES = ["measure", "cx", "id", "rz", "sx", "x"]
generate_preset_pass_manager(optimization_level=2, basis_gates=CORE_BASIS_GATES)

# 创建采样器并运行电路
sampler = Sampler(mode=aer)
job = sampler.run([qc], shots=1024)

# 获取结果
result = job.result()
pub_result = result[0]

# 提取每次测量的结果
counts = pub_result.data.c.get_counts()
print("Measurement counts:", counts)


     ┌───┐┌─┐┌───┐     ┌─┐┌───┐     ┌─┐┌───┐     ┌─┐┌───┐     ┌─┐┌───┐     ┌─┐»
q_0: ┤ H ├┤M├┤ H ├─────┤M├┤ H ├─────┤M├┤ H ├─────┤M├┤ H ├─────┤M├┤ H ├─────┤M├»
     ├───┤└╥┘├───┤┌───┐└╥┘├───┤┌───┐└╥┘├───┤┌───┐└╥┘├───┤┌───┐└╥┘├───┤┌───┐└╥┘»
q_1: ┤ H ├─╫─┤ H ├┤ H ├─╫─┤ H ├┤ H ├─╫─┤ H ├┤ H ├─╫─┤ H ├┤ H ├─╫─┤ H ├┤ H ├─╫─»
     ├───┤ ║ ├───┤├───┤ ║ ├───┤├───┤ ║ ├───┤├───┤ ║ ├───┤├───┤ ║ ├───┤├───┤ ║ »
q_2: ┤ H ├─╫─┤ H ├┤ H ├─╫─┤ H ├┤ H ├─╫─┤ H ├┤ H ├─╫─┤ H ├┤ H ├─╫─┤ H ├┤ H ├─╫─»
     └───┘ ║ └───┘└───┘ ║ └───┘└───┘ ║ └───┘└───┘ ║ └───┘└───┘ ║ └───┘└───┘ ║ »
q_3: ──────╫────────────╫────────────╫────────────╫────────────╫────────────╫─»
           ║            ║            ║            ║            ║            ║ »
q_4: ──────╫────────────╫────────────╫────────────╫────────────╫────────────╫─»
           ║            ║            ║            ║            ║            ║ »
c: 5/══════╩════════════╩════════════╩════════════╩════════════╩════════════╩═»
           0            0            0  

In [81]:
from qiskit import QuantumCircuit
from qiskit.quantum_info import Statevector

# 创建量子电路
num_qubits = 2
qc = QuantumCircuit(num_qubits)

# 添加量子门（示例）
qc.h(0)
qc.cx(0, 1)
# 获取理想状态向量
statevector = Statevector.from_instruction(qc)

# 计算理论概率分布
probabilities = statevector.probabilities()
import numpy as np
print(np.count_nonzero(probabilities))
# 打印结果
print(probabilities)


2
[0.5 0.  0.  0.5]


In [67]:
from qiskit import QuantumCircuit
from qiskit_aer import AerSimulator
from qiskit.transpiler.preset_passmanagers import generate_preset_pass_manager
from qiskit_ibm_runtime import SamplerV2 as Sampler
qc = QuantumCircuit(2, 2)
qc.x(1)
qc.measure(range(2),range(2))
qc.h(0)
qc.measure(range(2),range(2))
qc.x(0)
qc.measure(range(2),range(2))
# qc.measure_all()
print(qc.draw())
aer = AerSimulator()
CORE_BASIS_GATES = ["measure", "cx", "id", "rz", "sx", "x"]
generate_preset_pass_manager(optimization_level=2, basis_gates=CORE_BASIS_GATES,)

sampler = Sampler(mode=aer)
job = sampler.run([qc], shots=1024)
result = job.result()
pub_result = result[0]
counts = pub_result.data.c.get_counts()
print(counts)

          ┌─┐┌───┐┌─┐┌───┐   ┌─┐
q_0: ─────┤M├┤ H ├┤M├┤ X ├───┤M├
     ┌───┐└╥┘└┬─┬┘└╥┘└┬─┬┘┌─┐└╥┘
q_1: ┤ X ├─╫──┤M├──╫──┤M├─┤M├─╫─
     └───┘ ║  └╥┘  ║  └╥┘ └╥┘ ║ 
c: 2/══════╩═══╩═══╩═══╩═══╩══╩═
           0   1   0   1   1  0 
{'11': 535, '10': 489}


In [58]:
from qiskit import QuantumCircuit, Aer, execute
from qiskit.quantum_info import Statevector

# 创建量子电路
num_qubits = 10  # 可以调整为较小的量子比特数量
qc = QuantumCircuit(num_qubits)

# 添加量子门（示例）
qc.h(0)
for x in range(num_qubits):
    qc.h(x)
qc.cx(0, 1)

# 使用Aer模拟器计算状态向量
backend = Aer.get_backend('statevector_simulator')
job = execute(qc, backend)
result = job.result()
statevector = result.get_statevector()

# 计算理论概率分布
probabilities = statevector.probabilities()

# 打印非零概率的计数和概率分布
import numpy as np
print(np.count_nonzero(probabilities))
print(probabilities)


ImportError: cannot import name 'Aer' from 'qiskit' (/home/jiangqifan/Tools/anaconda3/envs/choco/lib/python3.10/site-packages/qiskit/__init__.py)

In [42]:
from qiskit import QuantumCircuit
from qiskit_aer import AerSimulator
from qiskit.transpiler.preset_passmanagers import generate_preset_pass_manager
from qiskit_ibm_runtime import SamplerV2 as Sampler
qc = QuantumCircuit(2, 2)
qc.x(1)
qc.measure(range(2),range(2))
qc.h(0)
qc.measure(range(2),range(2))
qc.x(0)
qc.measure(range(2),range(2))
# qc.measure_all()
print(qc.draw())
aer = AerSimulator()
CORE_BASIS_GATES = ["measure", "cx", "id", "rz", "sx", "x"]
generate_preset_pass_manager(optimization_level=2, basis_gates=CORE_BASIS_GATES,)

sampler = Sampler(mode=aer)
job = sampler.run([qc], shots=1024)
result = job.result()
pub_result = result[0]
counts = pub_result.data.c.get_counts()
print(counts)

          ┌─┐┌───┐┌─┐┌───┐   ┌─┐
q_0: ─────┤M├┤ H ├┤M├┤ X ├───┤M├
     ┌───┐└╥┘└┬─┬┘└╥┘└┬─┬┘┌─┐└╥┘
q_1: ┤ X ├─╫──┤M├──╫──┤M├─┤M├─╫─
     └───┘ ║  └╥┘  ║  └╥┘ └╥┘ ║ 
c: 2/══════╩═══╩═══╩═══╩═══╩══╩═
           0   1   0   1   1  0 
{'11': 508, '10': 516}


In [ ]:
from qiskit import QuantumCircuit
from qiskit_aer import AerSimulator
from qiskit.transpiler.preset_passmanagers import generate_preset_pass_manager
from qiskit_ibm_runtime import SamplerV2 as Sampler
qc = QuantumCircuit(2, 2)
qc.x(1)
qc.measure(range(2),range(2))
qc.h(0)
qc.measure(range(2),range(2))
qc.x(0)
qc.measure(range(2),range(2))
# qc.measure_all()
print(qc.draw())
aer = AerSimulator()
CORE_BASIS_GATES = ["measure", "cx", "id", "rz", "sx", "x"]
generate_preset_pass_manager(optimization_level=2, basis_gates=CORE_BASIS_GATES,)

sampler = Sampler(mode=aer)
job = sampler.run([qc], shots=1024)
result = job.result()
pub_result = result[0]
counts = pub_result.data.c.get_counts()
print(counts)

In [ ]:
from qiskit import QuantumCircuit
from qiskit_aer import AerSimulator
from qiskit.transpiler.preset_passmanagers import generate_preset_pass_manager
from qiskit_ibm_runtime import SamplerV2 as Sampler
qc = QuantumCircuit(2, 2)
qc.x(1)
qc.measure(range(2),range(2))
qc.h(0)
qc.measure(range(2),range(2))
qc.x(0)
qc.measure(range(2),range(2))
# qc.measure_all()
print(qc.draw())
aer = AerSimulator()
CORE_BASIS_GATES = ["measure", "cx", "id", "rz", "sx", "x"]
generate_preset_pass_manager(optimization_level=2, basis_gates=CORE_BASIS_GATES,)

sampler = Sampler(mode=aer)
job = sampler.run([qc], shots=1024)
result = job.result()
pub_result = result[0]
counts = pub_result.data.c.get_counts()
print(counts)

In [5]:
from qiskit import QuantumCircuit

# 创建第一个电路
qc1 = QuantumCircuit(2)
qc1.h(0)  # 在第一个量子比特上应用Hadamard门

# 创建第二个电路
qc2 = QuantumCircuit(2)
qc2.cx(0, 1)  # 在第一个和第二个量子比特之间应用CNOT门

# 连接两个电路
qc1.compose(qc2, inplace=True)

# 绘制最终电路
qc1.draw()


┌───┐     
q_0: ┤ H ├──■──
     └───┘┌─┴─┐
q_1: ─────┤ X ├
          └───┘

In [14]:
from qiskit import QuantumCircuit, QuantumRegister

# 创建第一个电路，包含2个量子比特
qc1 = QuantumCircuit(2)
qc1.h(0)  # 在第一个量子比特上应用Hadamard门

# 创建第二个电路，包含3个量子比特
qc2 = QuantumCircuit(3)
qc2.cx(0, 1)  # 在第一个和第二个量子比特之间应用CNOT门
qc2.cx(1, 2)  # 在第二个和第三个量子比特之间应用CNOT门
qc1.measure_all()
# 在第一个电路中添加一个量子寄存器，以便可以连接第二个电路
qc1.add_register(QuantumRegister(1, 'q2'))  # 添加一个量子比特

# 连接两个电路
qc1.compose(qc2, qubits=[0, 1, 2], inplace=True)

# 绘制最终电路
qc1.draw()


┌───┐ ░ ┌─┐             
   q_0: ┤ H ├─░─┤M├─────■───────
        └───┘ ░ └╥┘┌─┐┌─┴─┐     
   q_1: ──────░──╫─┤M├┤ X ├──■──
              ░  ║ └╥┘└───┘┌─┴─┐
    q2: ─────────╫──╫──────┤ X ├
                 ║  ║      └───┘
meas: 2/═════════╩══╩═══════════
                 0  1

In [ ]:
from qiskit import QuantumCircuit
from qiskit_aer import AerSimulator
from qiskit.transpiler.preset_passmanagers import generate_preset_pass_manager
from qiskit_ibm_runtime import SamplerV2 as Sampler
qc = QuantumCircuit(2, 2)
qc.x(1)
qc.measure(range(2),range(2))
qc.h(0)
qc.measure(range(2),range(2))
qc.x(0)
qc.measure(range(2),range(2))
# qc.measure_all()
print(qc.draw())
aer = AerSimulator()
CORE_BASIS_GATES = ["measure", "cx", "id", "rz", "sx", "x"]
generate_preset_pass_manager(optimization_level=2, basis_gates=CORE_BASIS_GATES,)

sampler = Sampler(mode=aer)
job = sampler.run([qc], shots=1024)
result = job.result()
pub_result = result[0]
counts = pub_result.data.c.get_counts()
print(counts)

In [1]:
from choco.model.lin_constr_bin_opt import LinearConstrainedBinaryOptimization as Model
if __name__ == '__main__':
    m = Model()
    num_facilities = 2
    num_demands = 2
    # m.addVar(name='jqf')
    x = m.addVars(num_facilities, name="x")
    y = m.addVars(num_demands, num_facilities, name="y")
    m.setObjective(sum(3 * y[i, j] * x[j] for i in range(num_demands) for j in range(num_facilities)) + sum(4 * x[j] for j in range(num_facilities)), 'min')

    m.addConstrs((x[j] + y[i, j] >= 1 for i in range(num_demands) for j in range(num_facilities)))
    obj = m.generate_obj_function()
    print(m)
    print(m.obj_dct)
    print(m.lin_constr_mtx)
    print("变量全取1结果:")
    print(obj([1] * len(m.variables)))
    print("最优解 by gurobi")
    print(m.get_best_cost())
    # m.optimize()
    

m:
variables:
x_0 (type: binary)   x_1 (type: binary)   y_0_0 (type: binary)   y_0_1 (type: binary)   y_1_0 (type: binary)   y_1_1 (type: binary)   slk_1_0 (type: binary)   slk_2_0 (type: binary)   slk_3_0 (type: binary)   slk_4_0 (type: binary)

obj:
min 3 * x_0 * y_0_0 + 3 * x_1 * y_0_1 + 3 * x_0 * y_1_0 + 3 * x_1 * y_1_1 + 4 * x_0 + 4 * x_1

s.t.:
1 * x_0 + 1 * y_0_0 + -1 * slk_1_0 == 1
1 * x_1 + 1 * y_0_1 + -1 * slk_2_0 == 1
1 * x_0 + 1 * y_1_0 + -1 * slk_3_0 == 1
1 * x_1 + 1 * y_1_1 + -1 * slk_4_0 == 1


{2: [([0, 2], 3), ([1, 3], 3), ([0, 4], 3), ([1, 5], 3)], 1: [([0], 4), ([1], 4)]}
[[ 1  0  1  0  0  0 -1  0  0  0  1]
 [ 0  1  0  1  0  0  0 -1  0  0  1]
 [ 1  0  0  0  1  0  0  0 -1  0  1]
 [ 0  1  0  0  0  1  0  0  0 -1  1]]
变量全取1结果:
20
最优解 by gurobi
Restricted license - for non-production use only - expires 2025-11-24
0.0


In [8]:
from choco.model.lin_constr_bin_opt import LinearConstrainedBinaryOptimization as Model
if __name__ == '__main__':
    m = Model()
    num_facilities = 1
    num_demands = 1
    m.addVar(name='jqf')
    x = m.addVars(num_facilities, name="x")
    y = m.addVars(num_demands, num_facilities, name="y")
    m.setObjective(sum(3 * y[i, j] for i in range(num_demands) for j in range(num_facilities)) + sum(4 * x[j] for j in range(num_facilities)), 'min')
    print("自动转不等式约束测试")
    m.addConstrs((x[j] <= 2 for i in range(num_demands) for j in range(num_facilities)))
    m.addConstrs((-2 <= -x[j] for i in range(num_demands) for j in range(num_facilities)))
    m.addConstrs((x[j] >= -1 for i in range(num_demands) for j in range(num_facilities)))
    m.addConstrs((x[j] >= 1 for i in range(num_demands) for j in range(num_facilities)))
    m.addConstrs((y[i, j] + x[j] <=  2 for i in range(num_demands) for j in range(num_facilities)))
    m.addConstrs((y[i, j] + x[j] + 10 >=  10 for i in range(num_demands) for j in range(num_facilities)))
    m.addConstrs((y[i, j] + x[j] + 10 >=  -10 for i in range(num_demands) for j in range(num_facilities)))
    m.addConstrs((y[i, j] + x[j] + 10 >=  11 for i in range(num_demands) for j in range(num_facilities)))
    m.addConstrs((y[i, j] + x[j] + 10 >=  13 for i in range(num_demands) for j in range(num_facilities)))
    m.addConstrs((10 >= 13 - y[i, j] - x[j] for i in range(num_demands) for j in range(num_facilities)))
    obj = m.generate_obj_function()
    # m.optimize()
    print(m)

自动转不等式约束测试
m:
variables:
jqf (type: binary)   x_0 (type: binary)   y_0_0 (type: binary)   slk_1_0 (type: binary)   slk_2_0 (type: binary)   slk_3_0 (type: binary)   slk_5_0 (type: binary)   slk_5_1 (type: binary)   slk_6_0 (type: binary)   slk_6_1 (type: binary)   slk_7_0 (type: binary)   slk_7_1 (type: binary)   slk_8_0 (type: binary)

obj:
min 3 * y_0_0 + 4 * x_0

s.t.:
1 * x_0 + 1 * slk_1_0 == 1
-1 * x_0 + -1 * slk_2_0 == -1
1 * x_0 + -1 * slk_3_0 == 0
1 * x_0 == 1
1 * y_0_0 + 1 * x_0 + 1 * slk_5_0 + 1 * slk_5_1 == 2
1 * y_0_0 + 1 * x_0 + -1 * slk_6_0 + -1 * slk_6_1 == 0
1 * y_0_0 + 1 * x_0 + -1 * slk_7_0 + -1 * slk_7_1 == 0
1 * y_0_0 + 1 * x_0 + -1 * slk_8_0 == 1
1 * y_0_0 + 1 * x_0 == 3
-1 * y_0_0 + -1 * x_0 == -3


